In [6]:
import pandas as pd
df = pd.read_csv(
    "all_sites_weekly_2020_2021.csv", dtype={"GEOID": "str"}, parse_dates=["week_date", "last_updated"]
)
df = df[df.city == 'Cincinnati, OH'].reset_index(drop=True)

In [7]:
import json
import plotly.express as px
import plotly.graph_objects as go
import os

# Load the GeoJSON file
with open('Hamilton_County_Census_Tracts_(2020).geojson') as f:
    geojson_data = json.load(f)

# Extract the features and create a list of properties
features = geojson_data['features']
properties = [feature['properties'] for feature in features]

# Define the center of the map and the zoom level
map_center = {'lat': 39.1031, 'lon': -84.5120}
map_zoom = 10
grouped_df = df.groupby("GEOID").agg({"filings_2020": "sum"}).reset_index()

# Create a choropleth map
fig = px.choropleth_mapbox(
    grouped_df,
    geojson=geojson_data,
    color='filings_2020',
    locations='GEOID',
    featureidkey='properties.GEOID',
    center=map_center,
    zoom=map_zoom,
    mapbox_style='mapbox://styles/mapbox/light-v10',
    opacity=0.8,
    hover_data={'GEOID': True, 'filings_2020': True}
)

# Customize the tooltip
fig.update_traces(hovertemplate='<b>%{customdata[0]}</b><br>' +
                                 'Filings 2020: %{customdata[1]}<br>')

# Set the map layout
fig.update_layout(
    mapbox={'accesstoken': os.environ.get('mapbox_access_token'), 'domain': {'x': [0, 1], 'y': [0, 1]}},
    margin={'l': 0, 'r': 0, 't': 0, 'b': 0},
    dragmode=False
)

# Show the figure
fig.show()